In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import scipy.stats as stats

from scipy.stats import zscore
from sklearn.mixture import GaussianMixture

from utils.samples import USED_SAMPLES, REPROGRAMMED_SAMPLES

In [2]:
df = pd.read_parquet("/app/data")

In [3]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 200)

In [4]:
# Defaults
COLUMN_GENE = "ID_REF"
COLUMN_TISSUE_SAMPLE = "TISSUE_SAMPLE"
COLUMN_TISSUE_NAME = "tissue_name"
COLUMN_NORM_VALUE = "VALUE"

# Filtering values for the gene expression analysis - see the last section
SHARE_HIGHLY_EXPRESSED: float = 0.99
SHARE_NEGATIVELY_EXPRESSED: float = 0.80

# Basic stats

In [5]:
df.head()

ID_REF     VALUE TISSUE_SAMPLE
0  GE_BrightCorner -1.464279    GSM1215621
1       DarkCorner -0.818223    GSM1215621
2     A_23_P326296  1.030766    GSM1215621
3     A_24_P287941  0.809299    GSM1215621
4     A_24_P325046 -0.354319    GSM1215621

In [6]:
df.shape

(8025899, 3)

In [7]:
# Get sample counts
df_counts = df.groupby(by="TISSUE_SAMPLE").agg(sample_count=("ID_REF", "count")).reset_index()
df_counts.head(30)

TISSUE_SAMPLE  sample_count
0     GSM1215621         42536
1     GSM1215622         42536
2     GSM1215623         42536
3     GSM1215624         42536
4     GSM1215625         42536
5     GSM1215626         42536
6     GSM1215627         42536
7     GSM1215628         42536
8     GSM1215629         42536
9     GSM1215630         42536
10    GSM1215631         42536
11    GSM1215632         42536
12    GSM1215633         42536
13    GSM1215634         42536
14    GSM1215635         42536
15    GSM1215636         42536
16    GSM1215637         42536
17    GSM1215638         42536
18    GSM1215639         42536
19    GSM1215640         42536
20    GSM1215641         42536
21    GSM1215642         42536
22    GSM1215643         42536
23    GSM1215644         42536
24    GSM1215645         42536
25    GSM1215646         42536
26    GSM1215647         42536
27    GSM1215648         42536
28    GSM1215649         42536
29    GSM1215650         42536

Mouse embryonic tissues have more samples. Omitting them for the time being.

In [8]:
# Select tissues
mask_tissues = df["TISSUE_SAMPLE"].isin(list(USED_SAMPLES.keys()))
df = df[mask_tissues]

In [9]:
# Bring in samples
df_samples = (
    pd.DataFrame
    .from_dict(USED_SAMPLES, orient="index", columns=["tissue_name"])
    .reset_index()
    .rename(columns={"index": "TISSUE_SAMPLE"})
    )

df = df.merge(
    df_samples,
    on="TISSUE_SAMPLE",
    how="left"
)

In [10]:
# Add repgromming flag
df["reprogrammed"] = df["tissue_name"].str.contains("_OSKM_").astype(int)

In [11]:
# Get tissues and genes
tissues = df["TISSUE_SAMPLE"].unique()
genes = df["ID_REF"].unique()

In [12]:
# This should match the # of unique rows for non mouse samples
len(genes)

42536

In [13]:
import plotly.graph_objects as go

# Calculate mean and std for each group
group_stats = df.groupby('tissue_name')['VALUE'].agg(['mean', 'median', 'std', 'min', 'max']).reset_index()

# Create Plotly plot
fig = go.Figure()

# Add bar for mean
fig.add_trace(go.Bar(
    x=group_stats['tissue_name'],
    y=group_stats['mean'],
    name='Mean',
    error_y=dict(type='data', array=group_stats['std'])
))

# Customize layout
fig.update_layout(title='Mean and Standard Deviation by tissue_name', xaxis_title='tissue_name', yaxis_title='VALUE')

fig.show()

In [14]:
# Create Plotly plot
fig = go.Figure()

# Add scatter plot for mean
fig.add_trace(go.Scatter(
    x=group_stats['tissue_name'],
    y=group_stats['mean'],
    mode='markers',
    name='Mean'
))

# Add scatter plot for median
fig.add_trace(go.Scatter(
    x=group_stats['tissue_name'],
    y=group_stats['median'],
    mode='markers',
    name='Median'
))

# Add scatter plot for min
fig.add_trace(go.Scatter(
    x=group_stats['tissue_name'],
    y=group_stats['min'],
    mode='markers',
    name='Min'
))

# Add scatter plot for max
fig.add_trace(go.Scatter(
    x=group_stats['tissue_name'],
    y=group_stats['max'],
    mode='markers',
    name='Max'
))

# Customize layout
fig.update_layout(
    title='Mean, Median, Min, and Max by tissue_name',
    xaxis_title='tissue_name',
    yaxis_title='VALUE',
    xaxis=dict(
        tickmode='array',
        tickvals=group_stats['tissue_name'],
        ticktext=[
            '<b>{}</b>'.format(sample) if 'OSKM' in sample else sample 
            for sample in group_stats['tissue_name']
        ]
    ),
    height=800
    )

fig.show()

Distributions not directly comparable based on the above plot

**NOTE** The above plot is quite similar to a box plot, but much faster to compute at leat when using plotly.

## Test for a single case

**Tissue:** GSM1215705  
**Gene:** A_24_P325046  

In [15]:
test_tissue = "GSM1215634"
test_gene = "A_24_P325046"

mask_test_tissue = df["TISSUE_SAMPLE"] == test_tissue
mask_test_gene = df["ID_REF"] == test_gene

df_test_tissue = df[mask_test_tissue].copy()
df_test_gene = df[mask_test_gene].copy()

In [16]:
# Creating a histogram using Plotly Express
fig = px.histogram(df_test_tissue, x='VALUE')

# Customize the layout
fig.update_layout(
    title_text=f'Normalized value gene histogram for tissue={test_tissue}',
    xaxis_title_text='Value', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

We should probably run distribution checks per tissue and use appropriate measure to normalize: https://bmcbioinformatics.biomedcentral.com/articles/10.1186/s12859-020-03892-w

In [17]:
# Assuming 'df' is your DataFrame and it has a 'VALUE' column for each 'TISSUE_SAMPLE'
def test_bimodal(sample_values):
    """
    Test if the distribution of the sample values is bimodal.
    """
    sample_values = sample_values.reshape(-1, 1)

    # Fit a Gaussian Mixture Model with 1 component
    gmm1 = GaussianMixture(n_components=1, random_state=0).fit(sample_values)
    aic1 = gmm1.aic(sample_values)

    # Fit a Gaussian Mixture Model with 2 components
    gmm2 = GaussianMixture(n_components=2, random_state=0).fit(sample_values)
    aic2 = gmm2.aic(sample_values)

    # If the AIC is significantly lower for 2 components, it suggests bimodality
    return aic2 < aic1


def test_distribution(sample_values, dist_name):
    """
    Test a sample against a specified distribution and return a goodness-of-fit measure.
    """
    if dist_name == 'normal':
        statistic, p_value = stats.shapiro(sample_values)
        return p_value > 0.05  # True if sample is likely normal
    elif dist_name == 'cauchy':
        # Fit to a Cauchy distribution and return goodness of fit (example: using KS test)
        params = stats.cauchy.fit(sample_values)
        statistic, p_value = stats.kstest(sample_values, 'cauchy', args=params)
        return p_value > 0.05
    elif dist_name == 'lognormal':
        # Similar approach as Cauchy
        params = stats.lognorm.fit(sample_values)
        statistic, p_value = stats.kstest(sample_values, 'lognorm', args=params)
        return p_value > 0.05
    elif dist_name == 'gamma':
        # Similar approach as Cauchy
        params = stats.gamma.fit(sample_values)
        statistic, p_value = stats.kstest(sample_values, 'gamma', args=params)
        return p_value > 0.05
    else:
        raise ValueError("Unknown distribution")


def analyze_distributions(df):
    results = []
    tissue_samples = df['TISSUE_SAMPLE'].unique()
    total_samples = len(tissue_samples)

    for index, tissue in enumerate(tissue_samples, start=1):
        print(f"Analyzing {index}/{total_samples}: TISSUE_SAMPLE = {tissue}")
        
        sample_values = df[df['TISSUE_SAMPLE'] == tissue]['VALUE'].dropna().to_numpy()
        
        result = {'TISSUE_SAMPLE': tissue}
        if test_bimodal(sample_values):
            result.update({dist: False for dist in ['normal', 'cauchy', 'lognormal', 'gamma']})
            result['bimodal'] = True
            print(f'\tDistribution=bimodal')
        else:
            for dist in ['normal', 'cauchy', 'lognormal', 'gamma']:
                print(f'\tFitting distribution: {dist}')
                result[dist] = test_distribution(sample_values, dist)
            result['bimodal'] = False
        
        results.append(result)

    return pd.DataFrame(results)

# Assuming you have a DataFrame 'df'
# df = pd.read_csv('your_data.csv')  # For example
results_df = analyze_distributions(df)

Analyzing 1/155: TISSUE_SAMPLE = GSM1215627
	Distribution=bimodal
Analyzing 2/155: TISSUE_SAMPLE = GSM1215628
	Distribution=bimodal
Analyzing 3/155: TISSUE_SAMPLE = GSM1215629
	Distribution=bimodal
Analyzing 4/155: TISSUE_SAMPLE = GSM1215630
	Distribution=bimodal
Analyzing 5/155: TISSUE_SAMPLE = GSM1215631
	Distribution=bimodal
Analyzing 6/155: TISSUE_SAMPLE = GSM1215632
	Distribution=bimodal
Analyzing 7/155: TISSUE_SAMPLE = GSM1215633
	Distribution=bimodal
Analyzing 8/155: TISSUE_SAMPLE = GSM1215634
	Distribution=bimodal
Analyzing 9/155: TISSUE_SAMPLE = GSM1215635
	Distribution=bimodal
Analyzing 10/155: TISSUE_SAMPLE = GSM1215636
	Distribution=bimodal
Analyzing 11/155: TISSUE_SAMPLE = GSM1215637
	Distribution=bimodal
Analyzing 12/155: TISSUE_SAMPLE = GSM1215638
	Distribution=bimodal
Analyzing 13/155: TISSUE_SAMPLE = GSM1215639
	Distribution=bimodal
Analyzing 14/155: TISSUE_SAMPLE = GSM1215640
	Distribution=bimodal
Analyzing 15/155: TISSUE_SAMPLE = GSM1215641
	Distribution=bimodal
Anal

/usr/local/lib/python3.11/site-packages/scipy/stats/_morestats.py:1882: UserWarning:

p-value may not be accurate for N > 5000.

/usr/local/lib/python3.11/site-packages/scipy/stats/_continuous_distns.py:6111: RuntimeWarning:

invalid value encountered in log



	Fitting distribution: gamma
Analyzing 27/155: TISSUE_SAMPLE = GSM1215653
	Distribution=bimodal
Analyzing 28/155: TISSUE_SAMPLE = GSM1215654
	Distribution=bimodal
Analyzing 29/155: TISSUE_SAMPLE = GSM1215655
	Distribution=bimodal
Analyzing 30/155: TISSUE_SAMPLE = GSM1215656
	Distribution=bimodal
Analyzing 31/155: TISSUE_SAMPLE = GSM1215657
	Distribution=bimodal
Analyzing 32/155: TISSUE_SAMPLE = GSM1215658
	Distribution=bimodal
Analyzing 33/155: TISSUE_SAMPLE = GSM1215659
	Distribution=bimodal
Analyzing 34/155: TISSUE_SAMPLE = GSM1215660
	Distribution=bimodal
Analyzing 35/155: TISSUE_SAMPLE = GSM1215661
	Distribution=bimodal
Analyzing 36/155: TISSUE_SAMPLE = GSM1215662
	Distribution=bimodal
Analyzing 37/155: TISSUE_SAMPLE = GSM1215663
	Distribution=bimodal
Analyzing 38/155: TISSUE_SAMPLE = GSM1215664
	Distribution=bimodal
Analyzing 39/155: TISSUE_SAMPLE = GSM1215665
	Distribution=bimodal
Analyzing 40/155: TISSUE_SAMPLE = GSM1215666
	Distribution=bimodal
Analyzing 41/155: TISSUE_SAMPLE =

/usr/local/lib/python3.11/site-packages/scipy/stats/_morestats.py:1882: UserWarning:

p-value may not be accurate for N > 5000.

/usr/local/lib/python3.11/site-packages/scipy/stats/_continuous_distns.py:6111: RuntimeWarning:

invalid value encountered in log



	Fitting distribution: gamma
Analyzing 138/155: TISSUE_SAMPLE = GSM1215770
	Distribution=bimodal
Analyzing 139/155: TISSUE_SAMPLE = GSM1215771
	Distribution=bimodal
Analyzing 140/155: TISSUE_SAMPLE = GSM1215772
	Distribution=bimodal
Analyzing 141/155: TISSUE_SAMPLE = GSM1215773
	Distribution=bimodal
Analyzing 142/155: TISSUE_SAMPLE = GSM1215774
	Distribution=bimodal
Analyzing 143/155: TISSUE_SAMPLE = GSM1215775
	Distribution=bimodal
Analyzing 144/155: TISSUE_SAMPLE = GSM1215776
	Distribution=bimodal
Analyzing 145/155: TISSUE_SAMPLE = GSM1215777
	Distribution=bimodal
Analyzing 146/155: TISSUE_SAMPLE = GSM1215778
	Distribution=bimodal
Analyzing 147/155: TISSUE_SAMPLE = GSM1215779
	Distribution=bimodal
Analyzing 148/155: TISSUE_SAMPLE = GSM1215780
	Distribution=bimodal
Analyzing 149/155: TISSUE_SAMPLE = GSM1215781
	Distribution=bimodal
Analyzing 150/155: TISSUE_SAMPLE = GSM1215782
	Distribution=bimodal
Analyzing 151/155: TISSUE_SAMPLE = GSM1215783
	Distribution=bimodal
Analyzing 152/155: 

In [18]:
results_df[results_df["bimodal"] == False]

TISSUE_SAMPLE  normal  cauchy  lognormal  gamma  bimodal
25     GSM1215652   False   False      False  False    False
136    GSM1215769   False   False      False  False    False

Only two samples GSM1215652 and GSM1215769 do not seem bimodal. Then again, they do not seem to follow any of the chose distributions...

In [19]:
# Creating a histogram using Plotly Express
fig = px.histogram(df[df['TISSUE_SAMPLE'] == "GSM1215652"], x='VALUE')

# Customize the layout
fig.update_layout(
    title_text=f'Normalized value gene histogram for tissue=GSM1215652',
    xaxis_title_text='Value', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

In [20]:
# Creating a histogram using Plotly Express
fig = px.histogram(df[df['TISSUE_SAMPLE'] == "GSM1215769"], x='VALUE')

# Customize the layout
fig.update_layout(
    title_text=f'Normalized value gene histogram for tissue=GSM1215769',
    xaxis_title_text='Value', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

However, the plots seem bimodalish with some peculiar properties..

What if we compare with the total distribution

In [21]:
# Creating a histogram using Plotly Express
fig = px.histogram(df_test_gene, x='VALUE')

# Customize the layout
fig.update_layout(
    title_text=f'Histogram for gene={test_gene}',
    xaxis_title_text='Value', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    #bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

In [22]:
# Lets see about Dark and brightcorners
mask_control = df["ID_REF"].isin(["DarkCorner", "GE_BrightCorner"])
df_control = df[mask_control]

In [23]:
fig = px.histogram(df_control, x='VALUE', color="ID_REF")

# Customize the layout
fig.update_layout(
    title_text=f'Normalized value gene histogram for gene={test_gene}',
    xaxis_title_text='Value', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

In [24]:
# Explode and scatter plot
df_control_pivoted = df_control.pivot(index='TISSUE_SAMPLE', columns='ID_REF', values='VALUE').reset_index()
df_control_pivoted["control_mean"] = (df_control_pivoted["DarkCorner"] + df_control_pivoted["GE_BrightCorner"]) / 2

df_control_pivoted.head()

ID_REF TISSUE_SAMPLE  DarkCorner  GE_BrightCorner  control_mean
0         GSM1215627    0.204950        -0.947931     -0.371490
1         GSM1215628   -0.575288         0.021172     -0.277058
2         GSM1215629   -0.456816         0.102369     -0.177223
3         GSM1215630    1.181449         1.134607      1.158028
4         GSM1215631   -0.404789        -0.221998     -0.313394

In [25]:
# Creating the scatter plot
fig = px.scatter(df_control_pivoted, x='DarkCorner', y='GE_BrightCorner')

# Show the plot
fig.show()

In [26]:
def count_gene_expression_simple_threshold(
        df: pd.DataFrame,
        id_cols: list[str] = ["ID_REF"],
        value_col: str = "VALUE",
        threshold: float = 0.0
        ) -> pd.DataFrame:
    X = df.copy()
    X = (
        X
        .assign(gene_expressed=lambda x: (x[value_col] > threshold).astype(int))
        .groupby(id_cols)
        .agg(
            tissue_sample_count=("gene_expressed", "count"),
            gene_expressed_sum=("gene_expressed", "sum")
            )
        .reset_index()
    )
    return X


def count_gene_expression_column_threshold(
        df: pd.DataFrame,
        threshold_col: str,
        id_cols: list[str] = ["ID_REF"],
        value_col: str = "VALUE",
        ) -> pd.DataFrame:
    X = df.copy()
    X = (
        X
        .assign(gene_expressed=lambda x: (x[value_col] > x[threshold_col]).astype(int))
        .groupby(id_cols)
        .agg(
            tissue_sample_count=("gene_expressed", "count"),
            gene_expressed_sum=("gene_expressed", "sum")
            )
        .reset_index()
    )
    return X


def scale_to_range(group):
    min_val = group.min()
    max_val = group.max()
    return 2 * ((group - min_val) / (max_val - min_val)) - 1

In [27]:
df.head()

ID_REF     VALUE TISSUE_SAMPLE     tissue_name  reprogrammed
0  GE_BrightCorner -0.947931    GSM1215627  PrS1 KT001_007             0
1       DarkCorner  0.204950    GSM1215627  PrS1 KT001_007             0
2     A_23_P326296 -1.197716    GSM1215627  PrS1 KT001_007             0
3     A_24_P287941  0.272818    GSM1215627  PrS1 KT001_007             0
4     A_24_P325046  0.547120    GSM1215627  PrS1 KT001_007             0

In [28]:
# Bring in mean control values
df = df.merge(
    df_control_pivoted[["TISSUE_SAMPLE", "DarkCorner", "GE_BrightCorner", "control_mean"]],
    on="TISSUE_SAMPLE",
    how="left"
)

In [29]:
# Drop Dark and Bright corners
mask_control = df["ID_REF"].isin(["GE_BrightCorner", "DarkCorner"])
df = df[~mask_control]

In [30]:
# Apply scaling within each group
df["scaled_value"] = df.groupby("TISSUE_SAMPLE")["VALUE"].transform(scale_to_range)

In [31]:
X_simple = count_gene_expression_simple_threshold(df, value_col="scaled_value", id_cols=["ID_REF"], threshold=0.0)
X_column = count_gene_expression_column_threshold(df, threshold_col="control_mean", id_cols=["ID_REF", "reprogrammed"])

In [32]:
X_simple = count_gene_expression_simple_threshold(df, value_col="scaled_value", id_cols=["ID_REF"], threshold=0.0)

In [33]:
X_simple_not_scaled = count_gene_expression_simple_threshold(df, value_col="VALUE", id_cols=["ID_REF"], threshold=0.0)

In [34]:
X_simple.head()

ID_REF  tissue_sample_count  gene_expressed_sum
0     (+)E1A_r60_1                  155                  20
1     (+)E1A_r60_3                  155                  23
2  (+)E1A_r60_a104                  155                  25
3  (+)E1A_r60_a107                  155                  29
4  (+)E1A_r60_a135                  155                  29

In [35]:
fig = px.histogram(X_simple, x='gene_expressed_sum')

# Customize the layout
fig.update_layout(
    title_text=f'Gene expressed sum histogram based on simple filtering. # of tissues = {X_simple.iloc[0, 1]}. Threshold = 0.0',
    xaxis_title_text='Expressed sum', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    #bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

In [36]:
fig = px.histogram(X_simple_not_scaled, x='gene_expressed_sum')

# Customize the layout
fig.update_layout(
    title_text=f'Gene expressed sum histogram based on simple filtering. # of tissues = {X_simple_not_scaled.iloc[0, 1]} Threshold = 0.0',
    xaxis_title_text='Expressed sum', # xaxis label
    yaxis_title_text='Frequency', # yaxis label
    #bargap=0.2, # gap between bars of adjacent location coordinates
)

# Show the plot
fig.show()

In [37]:
X_simple

ID_REF  tissue_sample_count  gene_expressed_sum
0         (+)E1A_r60_1                  155                  20
1         (+)E1A_r60_3                  155                  23
2      (+)E1A_r60_a104                  155                  25
3      (+)E1A_r60_a107                  155                  29
4      (+)E1A_r60_a135                  155                  29
...                ...                  ...                 ...
42529     ETG09_205211                  155                  18
42530      ETG10_13482                  155                  18
42531     ETG10_195139                  155                  18
42532     ETG10_234183                  155                  22
42533     ETG10_236652                  155                  19

[42534 rows x 3 columns]

In [38]:
X_simple["gene_expressed_sum"].unique()

array([20, 23, 25, 29, 28, 27, 26, 41, 39, 34, 21, 30, 24, 19, 58, 48, 31,
       40, 62, 42, 46, 33, 54, 38, 35, 52, 22, 32, 65, 47, 63, 60, 45, 18,
       43, 53, 55, 49, 37, 36, 44, 59, 61, 57, 66, 17, 68, 50, 51, 56, 70,
       69, 67, 64, 71, 16, 72, 73, 77, 15, 13, 74, 14, 76, 11,  9, 75,  8])

In [39]:
X_column["gene_expressed_sum"].unique()

array([24, 52, 21, 40, 25, 41, 27, 51, 48, 28, 50, 26, 46, 29, 59, 22, 55,
       58,  9, 19, 38, 18, 31, 23, 45, 34, 37, 15, 60, 42, 43, 44, 13, 69,
       49, 61, 20, 10, 54, 30, 39, 35, 16, 47, 36, 32, 33, 53, 11, 66, 73,
       64, 14, 68, 62, 63, 57,  7, 65, 17, 12, 76, 56, 67, 72, 70, 77,  6,
        8, 74, 79, 80, 71,  5, 78,  0, 82,  4, 84,  3, 75, 81, 88, 85, 83,
        1,  2])

In [40]:
df.head()

ID_REF     VALUE TISSUE_SAMPLE     tissue_name  reprogrammed  \
2    A_23_P326296 -1.197716    GSM1215627  PrS1 KT001_007             0   
3    A_24_P287941  0.272818    GSM1215627  PrS1 KT001_007             0   
4    A_24_P325046  0.547120    GSM1215627  PrS1 KT001_007             0   
5    A_23_P200404  0.011409    GSM1215627  PrS1 KT001_007             0   
6  A_19_P00800513  0.151560    GSM1215627  PrS1 KT001_007             0   

   DarkCorner  GE_BrightCorner  control_mean  scaled_value  
2     0.20495        -0.947931      -0.37149     -0.273901  
3     0.20495        -0.947931      -0.37149     -0.118234  
4     0.20495        -0.947931      -0.37149     -0.089197  
5     0.20495        -0.947931      -0.37149     -0.145906  
6     0.20495        -0.947931      -0.37149     -0.131070

# Tests for expression thresholds

In [41]:
# Set thresholds
score_thresholds_two_tailed = {
    "90th_percentile": 1.64,
    "95th_percentile": 1.96,
    "99th_percentile": 2.58
}

quantile_thresholds_two_tailed = {
    "90th_percentile": 0.90,
    "95th_percentile": 0.95,
    "99th_percentile": 0.99
}

high_expression_filter = ('reprogrammed_share_highly_expressed', SHARE_HIGHLY_EXPRESSED)
negative_expression_filter = ('normal_share_negatively_expressed', SHARE_NEGATIVELY_EXPRESSED)

In [42]:
def prune_results(
        df: pd.DataFrame, 
        high_expression: tuple[str, float],
        negative_expression: tuple[str, float]
        ) -> pd.DataFrame:
    """
    Filters the DataFrame based on conditions for high and negative expression.

    This function prunes the input DataFrame by applying two filters: one for high expression and another for negative expression. 
    Rows are retained if they meet both conditions: their value in the column specified for high expression exceeds the 
    corresponding threshold, and their value in the column specified for negative expression exceeds its threshold.

    Parameters:
    df (pd.DataFrame): The input DataFrame to be pruned.
    high_expression (tuple[str, float]): A tuple containing the column name and threshold for high expression share.
    negative_expression (tuple[str, float]): A tuple containing the column name and threshold for negative expression share.

    Returns:
    pd.DataFrame: A pruned DataFrame containing rows that meet both high and negative expression criteria.
    """
    df = df.copy()
    mask = (
        (df[high_expression[0]] >= high_expression[1]) &
        (df[negative_expression[0]] >= negative_expression[1])
    )
    return df[mask]


def _get_expression_shares(
        df: pd.DataFrame,
        reprogrammed_tissues: dict[str, list[str]],
        column_score: str,
        high_threshold: float
        ) -> pd.DataFrame:
    # Process each key in reprogrammed tissues
    dictkey_cols = []
    for key, tissue_samples in reprogrammed_tissues.items():
        key_high_expr_col = f'{key}_highly_expressed'
        dictkey_cols.append(key_high_expr_col)
        
        # Find genes highly expressed in any of the tissue samples for this key
        mask_highly_expressed_in_key = (
            df[COLUMN_TISSUE_SAMPLE].isin(tissue_samples) & (df[column_score] > high_threshold)
        )
        highly_expressed_genes = df[mask_highly_expressed_in_key][COLUMN_GENE].unique()

        # Mark genes as 1 if they are highly expressed in any of the key's tissue samples
        df[key_high_expr_col] = df[COLUMN_GENE].isin(highly_expressed_genes).astype(int)

    # Calculate shares for normal and reprogrammed samples
    normal_sample_mask = df['reprogrammed'] == 0
    normal_negatively_expressed = df[normal_sample_mask].groupby(COLUMN_GENE)['negatively_expressed'].mean()
    df = df.join(normal_negatively_expressed, on=COLUMN_GENE, rsuffix='_normal_share')

    df = (df
        .rename(
            columns={'negatively_expressed_normal_share': 'normal_share_negatively_expressed'}
            )
        )

    df['reprogrammed_share_highly_expressed'] = df[dictkey_cols].mean(axis=1)

    return df


def z_score_analysis(
        df: pd.DataFrame,
        threshold: float = 1.96,
        reprogrammed_tissues: dict[str, list[str]] = REPROGRAMMED_SAMPLES,
        column_score: str = 'z_score'
        ) -> pd.DataFrame:
    """
    Performs z-score analysis on gene expression data to identify highly and negatively expressed genes.

    This function applies z-score thresholds to determine high and negative expression in a gene expression dataset.
    It adds columns indicating whether each gene is highly or negatively expressed based on the z-score. It also processes 
    specified reprogrammed tissues to identify genes that are highly expressed in any of the tissue samples for each given key.
    Additionally, it calculates the share of negatively expressed genes in normal samples and the share of highly expressed genes 
    in reprogrammed samples.

    Parameters:
    df (pd.DataFrame): The input DataFrame containing gene expression data.
    threshold (float, optional): The z-score threshold for defining high expression. Defaults to 1.96 (~95th percentile).
    reprogrammed_tissues (dict[str, list[str]], optional): A dictionary mapping keys to lists of tissue samples 
                                                            representing reprogrammed tissues.

    Returns:
    pd.DataFrame: The DataFrame with additional columns indicating high/negative expression and shares of expression in normal 
                  and reprogrammed samples.
    """
    
    df = df.copy()

    # Define thresholds for high and low expression
    high_threshold = threshold
    low_threshold = -1 * high_threshold

    df['z_score'] = df.groupby(COLUMN_TISSUE_SAMPLE)[COLUMN_NORM_VALUE].transform(zscore)

    df['highly_expressed'] = (df['z_score'] > high_threshold).astype(int)
    df['negatively_expressed'] = (df['z_score'] < low_threshold).astype(int)

    return _get_expression_shares(df, reprogrammed_tissues, column_score, high_threshold)


def bimodal_analysis(
        df: pd.DataFrame,
        threshold: float = 1.96,
        reprogrammed_tissues: dict[str, list[str]] = REPROGRAMMED_SAMPLES,
        column_score: str = 'bimodal_expression'
        ) -> pd.DataFrame:
    """
    Analyzes gene expression data to classify genes based on bimodal expression patterns and calculates the share 
    of highly and negatively expressed genes in each tissue sample.

    Parameters:
    df (pd.DataFrame): The input DataFrame containing gene expression data.
    value_column (str): The column name in df that contains the gene expression values to be analyzed.
    threshold (float, optional): The z-score threshold for defining high and low expression in each mode. Defaults to 1.96.

    Returns:
    pd.DataFrame: The DataFrame with additional columns indicating bimodal high, low, or normal expression for each tissue sample,
                  along with the share of highly and negatively expressed genes.
    """
    df = df.copy()
    tissue_samples = df['TISSUE_SAMPLE'].unique()

    # Define thresholds for high and low expression
    high_threshold = threshold
    low_threshold = -1 * high_threshold

    # Classify gene expression using bimodal models
    for tissue in tissue_samples:
        sample_values = df[df[COLUMN_TISSUE_SAMPLE] == tissue][COLUMN_NORM_VALUE]
        bimodal_labels = classify_expression_bimodal(sample_values, threshold)

        # Assuming 'ID_REF' is the identifier for each gene
        df.loc[df['TISSUE_SAMPLE'] == tissue, column_score] = bimodal_labels

    df['highly_expressed'] = (df['bimodal_expression'] > high_threshold).astype(int)
    df['negatively_expressed'] = (df['bimodal_expression'] < low_threshold).astype(int)

    return _get_expression_shares(df, reprogrammed_tissues, column_score, high_threshold)


def classify_expression_bimodal(sample_values: pd.Series | np.ndarray, threshold: float) -> list[str]:
    """
    Classifies each value in a sample as highly expressed, negatively expressed, or normally expressed in a bimodal distribution.

    The classification is based on a Gaussian Mixture Model with two components. Each value is assigned to a component (mode)
    and then classified as high, low, or normal based on its distance from the mean of its assigned mode.

    Parameters:
    sample_values (pd.Series | np.ndarray): An array or series of gene expression values to be classified.
    threshold (float, optional): The threshold (in standard deviations from the mean) for defining high and low expression. 
                                 Defaults to 1.96 (approximately the 95th percentile).

    Returns:
    list[str]: A list of labels ('bimodal_highly_expressed', 'bimodal_negatively_expressed', 'bimodal_normally_expressed') 
               for each value in sample_values.
    """
    # Reshape the data and fit a GMM with 2 components
    if isinstance(sample_values, pd.Series):
        sample_values = sample_values.to_numpy()
    sample_values_reshaped = sample_values.reshape(-1, 1)
    gmm = GaussianMixture(n_components=2, random_state=0).fit(sample_values_reshaped)

    # Predict the component each sample belongs to
    component_labels = gmm.predict(sample_values_reshaped)

    # Calculate mean and std for each component
    means = gmm.means_.flatten()
    stds = np.sqrt(gmm.covariances_.flatten())

    # Define thresholds for high and low expression for each mode
    high_thresholds = means + threshold * stds
    low_thresholds = means - threshold * stds

    # Classify each gene based on its mode and expression level
    expression_labels: list[float] = []
    for value, label in zip(sample_values, component_labels): # Should negativity be considerd here?
        if value > high_thresholds[label]:
            expression_labels.append(1.1 * threshold)
        elif value < low_thresholds[label]:
            expression_labels.append(-1.1 * threshold)
        else:
            expression_labels.append(0.0)

    return expression_labels


def quantile_analysis(
        df: pd.DataFrame,
        threshold: float = 0.95,
        reprogrammed_tissues: dict[str, list[str]] = REPROGRAMMED_SAMPLES,
        column_score:str = 'quantile_expression',
        lower_quantile: float = 0.05,
        upper_quantile: float = 0.95,
        ) -> pd.DataFrame:
    """
    Analyzes gene expression data to classify genes based on bimodal expression patterns and calculates the share 
    of highly and negatively expressed genes in each tissue sample.

    Parameters:
    df (pd.DataFrame): The input DataFrame containing gene expression data.
    value_column (str): The column name in df that contains the gene expression values to be analyzed.
    threshold (float, optional): The z-score threshold for defining high and low expression in each mode. Defaults to 1.96.

    Returns:
    pd.DataFrame: The DataFrame with additional columns indicating bimodal high, low, or normal expression for each tissue sample,
                  along with the share of highly and negatively expressed genes.
    """
    df = df.copy()
    tissue_samples = df['TISSUE_SAMPLE'].unique()

    # Classify gene expression using bimodal models
    for tissue in tissue_samples:
        sample_values = df[df[COLUMN_TISSUE_SAMPLE] == tissue][COLUMN_NORM_VALUE]
        quantile_labels = classify_quantiles(sample_values, threshold, lower_quantile, upper_quantile)

        # Assuming 'ID_REF' is the identifier for each gene
        df.loc[df[COLUMN_TISSUE_SAMPLE] == tissue, column_score] = quantile_labels
        # print(df[df[COLUMN_TISSUE_SAMPLE] == tissue].groupby(quantile_labels).count())

    df['highly_expressed'] = (df[column_score] > threshold).astype(int)
    df['negatively_expressed'] = (df[column_score] < -threshold).astype(int)

    return _get_expression_shares(df, reprogrammed_tissues, column_score, threshold)


def classify_quantiles(
        sample_values: pd.Series | np.ndarray,
        threshold: float,
        lower_quantile: float,
        upper_quantile: float
    ) -> pd.DataFrame:
    """
    Classifies each value in a sample as highly expressed, negatively expressed, or normally expressed based on quantiles.

    The classification uses the 25th and 75th quantiles (by default) to define thresholds for low and high expression. 
    Values above the upper quantile threshold are classified as 'highly_expressed', values below the lower quantile threshold 
    are classified as 'negatively_expressed', and values in between are classified as 'normally_expressed'.

    Parameters:
    sample_values (pd.Series | np.ndarray): An array or series of gene expression values to be classified.
    lower_quantile (float, optional): The lower quantile threshold for defining low expression. Defaults to 0.25.
    upper_quantile (float, optional): The upper quantile threshold for defining high expression. Defaults to 0.75.

    Returns:
    list[str]: A list of labels ('highly_expressed', 'negatively_expressed', 'normally_expressed') for each value in sample_values.
    """
    if isinstance(sample_values, pd.Series):
        sample_values = sample_values.to_numpy()
    # Define quantile thresholds
    high_threshold = np.quantile(sample_values, upper_quantile)
    low_threshold = np.quantile(sample_values, lower_quantile)

    # Classify each gene based on quantile thresholds
    expression_labels: list[float] = []
    for value in sample_values:
        if value > high_threshold:
            expression_labels.append(1.1 * threshold)
        elif value < low_threshold:
            expression_labels.append(-1.1 * threshold)
        else:
            expression_labels.append(0.0)
    return expression_labels


def grid_search(
        df: pd.DataFrame,
        lower_thresholds: np.ndarray,
        upper_thresholds: np.ndarray,
        reprogrammed_tissues: dict[str, list[str]] = REPROGRAMMED_SAMPLES,
        ) -> pd.DataFrame:
    df = df.copy()
    _high_expression_filter = ('reprogrammed_share_highly_expressed', 0.99)
    _negative_expression_filter = ('normal_share_negatively_expressed', 0.80)

    potential_gene_dfs: list[pd.DataFrame] = []
    for low_threshold in lower_thresholds:
        for high_threshold in upper_thresholds:
             # Define thresholds for high and low expression
                df['highly_expressed'] = (df[COLUMN_NORM_VALUE] > high_threshold).astype(int)
                df['negatively_expressed'] = (df[COLUMN_NORM_VALUE] < low_threshold).astype(int)
                df_current = prune_results(
                    _get_expression_shares(df, reprogrammed_tissues, COLUMN_NORM_VALUE, high_threshold),
                    _high_expression_filter,
                    _negative_expression_filter
                    )
                print(f'Iteration: ({low_threshold, high_threshold}. Df shape: {df_current.shape})')
                if df_current.shape[0] > 0:
                    print(
                        f'Lower/Upper thresholds set at: ({low_threshold}, {high_threshold})'
                        f'# of unique genes: {df_current[COLUMN_GENE].nunique()}'
                        )
                    if df_current[COLUMN_GENE].nunique() < 20:
                        print(f'Unique genes: {df_current[COLUMN_GENE].unique()}')
                    potential_gene_dfs.append(df_current)
    return potential_gene_dfs

## Z-scored based filtering of highly and negatively expressed genes

In [43]:
# Filtering
z_score_results: dict[str, pd.DataFrame] = dict()
for key, threshold in score_thresholds_two_tailed.items():
    print(f'Running z-score analysis for {key}~={threshold}')
    df_z_scores = z_score_analysis(df, threshold)
    df_pruned_z_scores = prune_results(df_z_scores, high_expression_filter, negative_expression_filter)

    z_score_results[key] = df_pruned_z_scores

    print(f'Left with {df_pruned_z_scores[COLUMN_GENE].nunique()} genes after pruning.')

Running z-score analysis for 90th_percentile~=1.64
Left with 2 genes after pruning.
Running z-score analysis for 95th_percentile~=1.96
Left with 2 genes after pruning.
Running z-score analysis for 99th_percentile~=2.58
Left with 2 genes after pruning.


In [44]:
for key, _df in z_score_results.items():
    print(f"{key}: {_df[COLUMN_GENE].unique()}")

90th_percentile: ['A_19_P00320354' 'A_33_P3843873']
95th_percentile: ['A_19_P00320354' 'A_33_P3843873']
99th_percentile: ['A_19_P00320354' 'A_33_P3843873']


## Bimodal distribution based filtering of highly and negatively expressed genes

In [45]:
df_bimodal = bimodal_analysis(df)

In [46]:
# Filtering
bimodal_results: dict[str, pd.DataFrame] = dict()
for key, threshold in score_thresholds_two_tailed.items():
    print(f'Running bimodal analysis for {key}~={threshold}')
    df_pruned_bimodal = prune_results(df_bimodal, high_expression_filter, negative_expression_filter)

    bimodal_results[key] = df_pruned_bimodal

    print(f'Left with {df_pruned_bimodal[COLUMN_GENE].nunique()} genes after pruning.')

Running bimodal analysis for 90th_percentile~=1.64
Left with 1 genes after pruning.
Running bimodal analysis for 95th_percentile~=1.96
Left with 1 genes after pruning.
Running bimodal analysis for 99th_percentile~=2.58
Left with 1 genes after pruning.


In [47]:
for key, _df in bimodal_results.items():
    print(f"{key}: {_df[COLUMN_GENE].unique()}")

90th_percentile: ['A_33_P3843873']
95th_percentile: ['A_33_P3843873']
99th_percentile: ['A_33_P3843873']


## Quantile based filtering of highly and negatively expressed genes

In [48]:
# Filtering
quantile_results: dict[str, pd.DataFrame] = dict()
for key, threshold in quantile_thresholds_two_tailed.items():
    print(f'Running quantile analysis for {key}~={threshold}')
    df_quantiles = quantile_analysis(df, threshold, lower_quantile=1-threshold, upper_quantile=threshold)
    df_pruned_quantiles = prune_results(df_quantiles, high_expression_filter, negative_expression_filter)

    quantile_results[key] = df_pruned_quantiles

    print(f'Left with {df_pruned_quantiles[COLUMN_GENE].nunique()} genes after pruning.')

Running quantile analysis for 90th_percentile~=0.9
Left with 12 genes after pruning.
Running quantile analysis for 95th_percentile~=0.95
Left with 4 genes after pruning.
Running quantile analysis for 99th_percentile~=0.99
Left with 2 genes after pruning.


In [49]:
for key, _df in quantile_results.items():
    print(f"{key}: {_df[COLUMN_GENE].unique()}")

90th_percentile: ['A_23_P41942' 'A_19_P00320354' 'A_23_P145006' 'A_19_P00812957'
 'A_23_P350005' 'A_23_P137484' 'A_24_P226508' 'A_23_P72817' 'A_24_P213478'
 'A_23_P16384' 'A_33_P3396527' 'A_33_P3843873']
95th_percentile: ['A_19_P00320354' 'A_23_P137484' 'A_23_P72817' 'A_33_P3843873']
99th_percentile: ['A_19_P00320354' 'A_33_P3843873']


## Grid search based filterig of highly and negatively expressed genes

In [50]:
lower_thresholds = np.arange(-4.7, -3.5, 0.1)
upper_thresholds = np.arange(5.5, 7.1, 0.1)
df_grid = grid_search(df, lower_thresholds, upper_thresholds)

Iteration: ((-4.7, 5.5). Df shape: (0, 18))
Iteration: ((-4.7, 5.6). Df shape: (0, 18))
Iteration: ((-4.7, 5.699999999999999). Df shape: (0, 18))
Iteration: ((-4.7, 5.799999999999999). Df shape: (0, 18))
Iteration: ((-4.7, 5.899999999999999). Df shape: (0, 18))
Iteration: ((-4.7, 5.999999999999998). Df shape: (0, 18))
Iteration: ((-4.7, 6.099999999999998). Df shape: (0, 18))
Iteration: ((-4.7, 6.1999999999999975). Df shape: (0, 18))
Iteration: ((-4.7, 6.299999999999997). Df shape: (0, 18))
Iteration: ((-4.7, 6.399999999999997). Df shape: (0, 18))
Iteration: ((-4.7, 6.4999999999999964). Df shape: (0, 18))
Iteration: ((-4.7, 6.599999999999996). Df shape: (0, 18))
Iteration: ((-4.7, 6.699999999999996). Df shape: (0, 18))
Iteration: ((-4.7, 6.799999999999995). Df shape: (0, 18))
Iteration: ((-4.7, 6.899999999999995). Df shape: (0, 18))
Iteration: ((-4.7, 6.999999999999995). Df shape: (0, 18))
Iteration: ((-4.6000000000000005, 5.5). Df shape: (0, 18))
Iteration: ((-4.6000000000000005, 5.6).